# Computer Programming 1105

In [ ]:
# Ignore this; my laptop is so old and Apple is nasty so I need this
sdkroot = !xcrun --show-sdk-path
%env SDKROOT={sdkroot[0]}

env: SDKROOT=/Library/Developer/CommandLineTools/SDKs/MacOSX.sdk


## Template theory and practice

Template is a way to write codes that has unknown types
but we have a very clear idea of what behavior we want.

Pair of the same type

```C++
template <typename T1>
struct Pair_same {
    T1 first;
    T1 second;
    Pair_same(const T1& a, const T1& b) : first(a), second(b) {} // constructor
    T1& operator[](int i) {
        if (i) return second;
        else return first;
    }
    const T1 operator[](int i) const {
        if (i) return second;
        else return first;
    }
};
```

Usage
```C++
Pair_same<int> p1(10, 20); // call constructor
Pair_same<int> p2 = {30, 40}; // similar to array initialization
cout << p1[0] << ", " << p1[1] << endl; // use [] to access
p1.first = 50; // modify first directly
p2[1] = 60; // use [] to modify second (because reference is returned)
```

The reason we need two `operator[];` is due to the following dilemma

- If we want to modify the value like `p2[1] = 60;`
  we need to return a reference.
- We need a const version to allow read-only access.
  This is because in `operator+`, we usually don't modify the operand.
  The keyword `const` in `operator+(const T other)`
  tells the compiler that we **promise** not to modify `other`.
  The compiler treat our promise very serious.
  So if in `operator+` we call the non-const version of `operator[]`,
  the compiler will complain.

There is no way we can achieve both in only one definition.

The std's `pair` is the with different types

```C++
template <typename T1, typename T2>
struct Pair_diff {
    T1 first;
    T2 second;
    Pair_diff(const T1& a, const T2& b) : first(a), second(b) {} // constructor
    T1& operator[](int i) {
        if (i) return second;
        else return first;
    }
    const T1 operator[](int i) const {
        if (i) return second;
        else return first;
    }
};

To define tuples of arbitrary length,
we need a feature of C++ called **variadic** templates/functions.

Some example of variadic functions like
`sum, max, min, average, printf, ...`

They are very hard to use and teach.
So we just use template containers.

## Container templates

C++ std library defines an array template
where the size is part of the template parameters.

```C++
template <typename T1, int size>
struct array {
    T1 elems[size];
    T1& operator[](int i) { return elems[i]; }
    const T1& operator[](int i) const { return elems[i]; }
};
```

Usages
```C++
array<int, 5> B;
B[0] = 10;
B[1] = 20;
cout << B[0] << ", " << B[1] << endl;
```

Now, when we defines functions, we can extract the size
as part of the template parameters.

```C++
template <typename T, int size>
T sum(array<T, size>& B) {
    T total = B[0];
    for (int i = 1; i < size; ++i) {
        total += B[i];
    }
    return total;
}

```

The vector template is perhaps more useful than array
because re can resize it.

This means that the size is no longer a template parameter.
You need to call a getter function to learn the size.

```C++
template <typename T1>
struct vector {
    T1* elems;
    int size;
    T1& operator[](int i) { return elems[i]; }
    int size() { return size; }
    vector(int s) : size(s) {
        elems = new T1[s];
    }
    ~vector{
        ...
    }
    void resize(int new_size) {
        T1* new_elems = new T1[new_size];
        int min_size = (new_size < size) ? new_size : size;
        for (int i = 0; i < min_size; i++)
            new_elems[i] = elems[i];
        delete[] elems;
        elems = new_elems;
        size = new_size;
    }
    T1 sum() {
        T1 total = elems[0];
        for (int i = 1; i < size; ++i) {
            total += elems[i];
        }
        return total;
    }
};
```

Or you can define `sum` outside of the `struct`:

```C++
template <typename T1>
T1 sum(vector<T1> a) {
    T1 total = a[0];
    for (int i = 1; i < a.size(); i++) {
        total += a[i];
    }
    return total;
}
```

## Doubley-linked list

```C++
std::list<int> fibo = {2, 3, 5, 13, 21};

auto b = fibo.begin();
fibo.insert(++ ++ ++b,  8);

for (auto f : fibo) {
    cout << f;
}
```

## Double-ended queue

```C++
std::deque<int> fibo = {3, 5, 8, 13};
    
fibo.push_front(2);
fibo.push_back(21);

for (auto f : fibo) {
    cout << f;
}

fibo.pop_front();
fibo.pop_back();
```

BTW, all containers support the `for auto` syntax.

```C++
for (auto x : B) {
    func(x);
}
```

is roughly equivalent to

```C++
for (auto it = B.begin(); it != B.end(); ++it) {
    func(*it);
}
```

In other words, the `for auto` syntax
works with any container that has `begin()` and `end()` methods.


## Priority queue

```C++
struct HW {
    string subject;
    int daysLeft;
    bool operator< (HW other) const {
        return daysLeft > other.daysLeft;
    }
};
std::priority_queue<HW> HwToDo;
HwToDo.push({"Linear Algebra", 5});
HwToDo.push({"Da 1 English", 3});
HwToDo.push({"Computer Prog", 7});

cout << "do this first" << HWToDo.top().subject;
```

```C++
std::set<string> playlist;
playlist.insert("To lightyear and beyond");
playlist.insert("A balloon suing white");
playlist.insert("Are you OK?");
playlist.insert("Actor");
playlist.insert("A balloon suing white");

cout << "top songs" << endl;
for (auto song : playlist) {
    cout << song << endl;
} // only four lines
```

```C++
std::multiset<string> playlist;
playlist.insert("To lightyear and beyond");
playlist.insert("A balloon called white");
playlist.insert("Are you OK?");
playlist.insert("Actor");
playlist.insert("A balloon called white");

cout << "top songs" << endl;
for (auto song : playlist) {
    cout << song << endl;
} // five lines
```

## Map (python dictionary)

```C++
std::map<std::string, int> city_population;

city_population["New York"] = 8419600;
city_population["Los Angeles"] = 3980400;
city_population["Chicago"] = 2716000;
city_population.insert(
    std::pair{"Houston", 2328000});

cout << "Population of New York: "
     << city_population["New York"] << endl;

for (auto pp : city_population) {
    cout << "City: " << pp.first
         << ", Population: " << pp.second << endl;
}
```

## Some words on iterators

iterator = how you are gonna visit things.

Forward iterator:
An iterator that lets you move forward
by overloading operator++;

Bidirectional iterator:
An iterator that lets you move both ways
by overloading both ++ and --.

random-access iterators:
An iterator that lets you [i]
by overloading operator[].


```C++
slink<int> L; // a singly-linked list
auto b = L.begin();
b++; // moving forward
cout << *b;

link<int> L; // a doubly-linked list
auto b = L.begin();
b++; // moving forward
b--; // moving backward
cout << *b;
```

For forward and bidirectional iterator;
If you want to find something,
Check everything.

```C++
auto find(T x) {
    for (auto p = L.begin(); p != L.end(); p++){
        if (*p == x) return p;
    }
    return p;
}
```

If you want to be able to use binary search, your iterator must support random access.

## find or check criteria

```C++
auto is11x = [](int n) {
    return n % 11 == 0;
}

std::find_if(fibo.begin(),fibo.end(), is11x);
std::count_if(fibo.begin(),fibo.end(), is11x);
```

## sorting


```C++
auto comparison_func = [](int a, int b) {
    if (a % 11 != b % 11) return a % 11 < b % 11;
    return a < b;
}
std::sort(fibo.begin(), fibo.end(), comparison_func);
```

## Container operations

```C++
std::vector<int> vec = {1, 2, 3, 4};
std::for_each(
    vec.begin(),
    vec.end(),
    [](int &n) { n *= n; }
);
// vec = {1, 4, 9, 16}
```

```C++
bool allEven = std::all_of(
    vec.begin(),
    vec.end(),
    [](int n) { return n % 2 == 0; }
);

bool allOdd = std::none_of(
    vec.begin(),
    vec.end(),
    [](int n) { return n % 2 == 0; }
);

bool containEven = std::any_of(
    vec.begin(),
    vec.end(),
    [](int n) { return n % 2 == 0; }
);
```

```C++
std::accumulate(
    numbers.begin(),
    numbers.end(),
    1,
    std::multiplies<int>()
);

std::accumulate(
    numbers.begin(),
    numbers.end(),
    0,
    std::plus<int>()
);
```

```C++
vector<int> numbers = {1, 2, 3, 4, 5};

std::accumulate(
    numbers.begin(),
    numbers.end(),
    0,
    [](int a, int b) {return a*b + a + b}
); // 719
```

## valarray

```C++
std::valarray<int> a = {1, 2, 3};
std::valarray<int> b = {10, 20, 30};

std::valarray<int> c = a + b;   // ✅ elementwise addition

for (int x : c) std::cout << x << ' ';
```

## Span


```C++
// g++ -std=c++20 demo.cpp
#include <span>
#include <vector>
#include <array>
#include <iostream>

int sum(std::span<const int> s) {
    int total = 0;
    for (int x : s) total += x;
    return total;
}

int main() {
    std::array<int, 5> a{10, 20, 30, 40, 50};
    std::vector<int> v{1, 2, 3, 4, 5};
    int c_arr[] = {6, 7, 8, 9, 10};

    std::span<int> whole_vec(v);           // view over vector storage
    std::span<int> sub = whole_vec.subspan(1, 3); // [2, 3, 4]
    std::cout << sum(sub) << '\n';         // 9

    std::cout << sum(a) << '\n';           // 150
    std::cout << sum(c_arr) << '\n';       // 40

    sub[0] = 42;                           // modifies v[1]
    std::cout << v[1] << '\n';             // 42
}
```

## Optional and expected

```C++
std::optional<int> opt;
opt = 42;
opt.reset();
if (opt.has_value())
    cout << "Value: " << opt.value() << endl;
else
    cout << "No value." << endl;
```


```C++

std::expected<int, std::string> safe_div(int a, int b) {
    if (b == 0) return std::unexpected("division by zero");
    return a / b;
}
```

## Variante and Any

```C++
std::variant<int, std::string> v;   // initially holds int{0}
v = 42;
std::cout << std::get<int>(v) << "\n";

v = "hello";
std::cout << std::get<std::string>(v) << "\n";
```

```C++
std::any X;

X = 42;
cout << std::any_cast<int>(X) << endl;
X = string("Hello, any");
cout << std::any_cast<string>(X) << endl;
```

## printf, nice to see you again

```C++
std::print("Default: {}\n", PI); // 3.141592653589793
std::print("Fixed:   {:.2f}\n", PI); // 3.14
std::print("Sci:     {:e}\n", PI); // 3.14e+00
std::print("Percent: {:.1%}\n", PI); // 314.2%
std::print("Dec: {}\n", 42); // 42
std::print("Bin: {:b}\n", 42); // 101010
std::print("Hex: {:X}\n", 42); // 2A
std::print("Prefixed: {:#x}\n", 42); // 0x2a
std::print("|{:>5}|\n", 42); // |   42|
std::print("|{:<5}|\n", 42); // |42   |
std::print("|{:05}|\n", 42); // |00042|
std::print("{:’}\n", 1234567); // 1,234,567
std::print("|{:>10.2f}|\n", x);  // right align, width 10, 2 decimals
std::print("|{:<10.2f}|\n", x);  // left align
std::print("|{:^10.2f}|\n", x);  // center align
std::print("|{:*>10.2f}|\n", x); // right align, pad with '*'
```

## Practices from last year

Complete the definitions of Polynomial and Matrix and overload related functions properly.

```C++

int main() {
    srand(time(NULL));
    Matrix<int, 2, 2> A;
    A[0][0] = rand() % 100;
    A[0][1] = rand() % 100;
    A[1][0] = rand() % 100;
    A[1][1] = rand() % 100;
    cout << "Matrix A is" << endl;
    cout << A << endl;
    Polynomial<int, 2> poly = A.char_poly();
    cout << "The characteristic polynomial of A is" << endl;
    cout << poly('x') << endl;
    cout << "P(-1) = " << poly(-1) << endl;
    cout << "P(0) = " << poly(0) << endl;
    cout << "P(1) = " << poly(1) << endl;
    cout << "P(A) is " << endl;
    cout << poly(A) << endl;
}


```

Finish the following program to test if your computer can do multi-threading.
Try to make the 
`B TS K TS TS B K TS`
sound at 240bpm.


```C++
#include <iostream>
#include <thread>
#include <chrono>
#include <mutex>
using namespace std;

std::mutex OnlyOneThreadCanRun;

// This is the "main" function for the B sound
void Bfunc() {
    std::this_thread::sleep_for(std::chrono::milliseconds(?));
    while (true) {
        OnlyOneThreadCanRun.lock();
        cout << "B" << endl;
        OnlyOneThreadCanRun.unlock();
        std::this_thread::sleep_for(std::chrono::milliseconds(?));
    }
}

// This is the "main" function for the TS sound
void TSfunc() {
    string indent = "          ";
    while(true) {
        OnlyOneThreadCanRun.lock();
        cout << indent << "TS" << endl;
        OnlyOneThreadCanRun.unlock();
        std::this_thread::sleep_for(std::chrono::milliseconds(?));
    }
}

// This is the "main" function for the K sound
void Kfunc() {
    std::this_thread::sleep_for(std::chrono::milliseconds(?));
    string indent = "                    ";
    while (true) {
        OnlyOneThreadCanRun.lock();
        cout << indent << "K" << endl;
        OnlyOneThreadCanRun.unlock();
        std::this_thread::sleep_for(std::chrono::milliseconds(?));
    }
}

// This is the mainest main function, the main function of all
int main() {
    std::thread Bthread(Bfunc);
    std::thread TSthread(TSfunc);
    std::thread Kthread(Kfunc);

    Bthread.join();
    TSthread.join();
    Kthread.join();

    cout << "All threads join the main thread.  Music ends." << endl;
}
```

In [1]:
%%bash
cat > bbox.cpp << CPPCODE

#include <iostream>
#include <thread>
#include <chrono>
#include <mutex>
using namespace std;

std::mutex OnlyOneThreadCanRun;

// This is the "main" function for the B sound
void Bfunc() {
    std::this_thread::sleep_for(std::chrono::milliseconds(250));
    while (true) {
        OnlyOneThreadCanRun.lock();
        cout << "B" << endl;
        OnlyOneThreadCanRun.unlock();
        std::this_thread::sleep_for(std::chrono::milliseconds(1000));
    }
}

// This is the "main" function for the TS sound
void TSfunc() {
    string indent = "          ";
    while(true) {
        OnlyOneThreadCanRun.lock();
        cout << indent << "TS" << endl;
        OnlyOneThreadCanRun.unlock();
        std::this_thread::sleep_for(std::chrono::milliseconds(500));
    }
}

// This is the "main" function for the K sound
void Kfunc() {
    std::this_thread::sleep_for(std::chrono::milliseconds(750));
    string indent = "                    ";
    while (true) {
        OnlyOneThreadCanRun.lock();
        cout << indent << "K" << endl;
        OnlyOneThreadCanRun.unlock();
        std::this_thread::sleep_for(std::chrono::milliseconds(1000));
    }
}

// This is the mainest main function, the main function of all
int main() {
    std::thread Bthread(Bfunc);
    std::thread TSthread(TSfunc);
    std::thread Kthread(Kfunc);

    Bthread.join();
    TSthread.join();
    Kthread.join();

    cout << "All threads join the main thread.  Music ends." << endl;
}

CPPCODE
g++-14 -std=c++26 -Wall -Wextra -Wpedantic -Wshadow -Wconversion bbox.cpp -o bbox
./bbox

          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
B
          TS
                    K
          TS
Process was interrupted.


CalledProcessError: Command 'b'cat > bbox.cpp << CPPCODE\n\n#include <iostream>\n#include <thread>\n#include <chrono>\n#include <mutex>\nusing namespace std;\n\nstd::mutex OnlyOneThreadCanRun;\n\n// This is the "main" function for the B sound\nvoid Bfunc() {\n    std::this_thread::sleep_for(std::chrono::milliseconds(250));\n    while (true) {\n        OnlyOneThreadCanRun.lock();\n        cout << "B" << endl;\n        OnlyOneThreadCanRun.unlock();\n        std::this_thread::sleep_for(std::chrono::milliseconds(1000));\n    }\n}\n\n// This is the "main" function for the TS sound\nvoid TSfunc() {\n    string indent = "          ";\n    while(true) {\n        OnlyOneThreadCanRun.lock();\n        cout << indent << "TS" << endl;\n        OnlyOneThreadCanRun.unlock();\n        std::this_thread::sleep_for(std::chrono::milliseconds(500));\n    }\n}\n\n// This is the "main" function for the K sound\nvoid Kfunc() {\n    std::this_thread::sleep_for(std::chrono::milliseconds(750));\n    string inden

## Multithreading

A program can launch multiple threads.

We can use one thread to do everything (what we have been doing).
Or we can ask different threads to perform different tasks.

Sometimes, multi-threading is favored over single-threading because it is faster.

When and why it is faster is hard to justify, though.
We need to go all the way to the architecture of computers.

![memory](byGPT.png)

As of 2024, modern computers have a memory hierarchy that looks like this ➡️

AI makes mistakes; don’t take this too seriously.

Also new technologies pop up every year so this table is probably already outdated.


Roughly speaking, there are fast but small memories near CPU (some are right inside CPU, some are right next to it).  We also have slow but large memories far away from CPU (some could be as far as cloud storage).

If CPU needs some data, it pulls them from far memory and store them in near memory.  And then it pulls the part it needs first and stores them in nearer memory, and so on.  This takes time.

When CPU is waiting for data movement, it can do something else.

Multi-threading is a way to tell CPU that you have two or three independent jobs, so when one thread is waiting for data, CPU can work on another threads that is handling independent data.

In [8]:
%%bash
cat > parallel.cpp <<'CPPCODE'
#include <bits/stdc++.h>
#include <omp.h>
using namespace std;

int main() {
    // keep N reasonably small for interactive runs
    const int N = 100000;
    vector<long long> A(N);
    for (int i = 0; i < N; ++i) A[i] = i;

    // parallel for must be inside a function (e.g., main)
    #pragma omp parallel for
    for (int i = 0; i < N; ++i) {
        A[i] *= A[i];
        int tid = omp_get_thread_num();
        // synchronize printing to avoid interleaved output
        #pragma omp critical
        cout << "thread #" << tid << " gets " << i << " -> " << A[i] << '\n';
    }

    return 0;
}
CPPCODE
# compile with OpenMP support and a modern standard
g++-14 -std=c++26 -O2 -fopenmp parallel.cpp -o parallel
./parallel


thread #12 gets 54550 -> 2975702500
thread #12 gets 54551 -> 2975811601
thread #7 gets 31822 -> 1012639684
thread #5 gets 22730 -> 516652900
thread #16 gets 72730 -> 5289652900
thread #19 gets 86365 -> 7458913225
thread #5 gets 22731 -> 516698361
thread #5 gets 22732 -> 516743824
thread #5 gets 22733 -> 516789289
thread #5 gets 22734 -> 516834756
thread #5 gets 22735 -> 516880225
thread #5 gets 22736 -> 516925696
thread #5 gets 22737 -> 516971169
thread #5 gets 22738 -> 517016644
thread #5 gets 22739 -> 517062121
thread #5 gets 22740 -> 517107600
thread #14 gets 63640 -> 4050049600
thread #12 gets 54552 -> 2975920704
thread #5 gets 22741 -> 517153081
thread #5 gets 22742 -> 517198564
thread #5 gets 22743 -> 517244049
thread #5 gets 22744 -> 517289536
thread #5 gets 22745 -> 517335025
thread #5 gets 22746 -> 517380516
thread #5 gets 22747 -> 517426009
thread #5 gets 22748 -> 517471504
thread #5 gets 22749 -> 517517001
thread #5 gets 22750 -> 517562500
thread #5 gets 22751 -> 517608001
t